In [2]:
import pandas as pd
import json
from pandas import json_normalize
import requests
from pathlib import Path
from multiprocessing.pool import ThreadPool as Pool
import codecs
import random
import re

In [3]:
URL_BASE = "https://arxiv.org/pdf/"
PDF_PATH = 'PDF'
TXT_PATH= 'TXT'

# Arxiv


In [4]:
data = pd.read_json('ARxiv/arxiv-metadata-oai-snapshot.json',lines=True, chunksize=2001,dtype={'id':'str'})
df = None
for i in data:
    df = i 
    print(type(i))
    break
df = df[['id','title','abstract']]
df.insert(3, "Text", "") 
df

<class 'pandas.core.frame.DataFrame'>


id                                              title  \
0     0704.0001  Calculation of prompt diphoton production cros...   
1     0704.0002           Sparsity-certifying Graph Decompositions   
2     0704.0003  The evolution of the Earth-Moon system based o...   
3     0704.0004  A determinant of Stirling cycle numbers counts...   
4     0704.0005  From dyadic $\Lambda_{\alpha}$ to $\Lambda_{\a...   
...         ...                                                ...   
1996  0704.1997  Query on Negative Temperature, Internal Intera...   
1997  0704.1998  Absence of the Fifth Force Problem in a Model ...   
1998  0704.1999  Dark matter caustics and the enhancement of se...   
1999  0704.2000  Search for a Higgs boson produced in associati...   
2000  0704.2001  Geometry of Parallelizable Manifolds in the Co...   

                                               abstract Text  
0       A fully differential calculation in perturba...       
1       We describe a new algorithm, the $(k,\ell)$-...       
2       The evolution of Earth-Moon system is descri...       
3       We show that a determinant of Stirling cycle...       
4       In this paper we show how to compute the $\L...       
...                                                 ...  ...  
1996    After negative temperature is restated, we f...       
1997    A scale invariant model containing dilaton $...       
1998    Cold dark matter haloes are populated by cau...       
1999    We describe a search for the standard model ...       
2000    In this paper, we deal with a generalization...       

[2001 rows x 4 columns]

In [7]:
def GetFileURL(file_id):
    url = URL_BASE+file_id
    r = requests.get(url, stream=True)    
    filename = Path(PDF_PATH+'/'+file_id+'.pdf')
    response = requests.get(url)
    filename.write_bytes(response.content)

In [35]:
pool_size = 16  
def worker(file):
    try:
        GetFileURL(file)
    except:
        print('error with item '+ file)
        try:
            with codecs.open(PDF_PATH+'/log.txt', 'a') as the_file:        
                the_file.writelines(str(file)+"\n")
        except:
            print('error en log '+ file)
def get_ids(iteracion,batch=100):    
    inicio = int(iteracion*batch)
    filesId = data[inicio :inicio + batch]['id']
    return filesId

pool = Pool(pool_size)
filesId = get_ids(19)
for file in filesId:
    pool.apply_async(worker, (file,))

pool.close()
pool.join()